In [272]:
import tensorflow as tf
import tensorflow_datasets as tfds
from tensorflow_datasets.image_classification import colorectal_histology
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Data fetching

In [273]:
(X_train, y_train),(X_val, y_val)= tfds.as_numpy(tfds.load(
    'colorectal_histology',
    split=["train[:80%]", "train[80%:]"],
    batch_size=-1,
    shuffle_files=True,
    as_supervised=True,
))

In [274]:
classes = colorectal_histology._CLASS_NAMES
classes, len(classes)

(('tumor',
  'stroma',
  'complex',
  'lympho',
  'debris',
  'mucosa',
  'adipose',
  'empty'),
 8)

In [275]:
rows, cols = 4, 4
img = [Image.fromarray(X_train[i], 'RGB') for i in range(rows*cols)]


fig = make_subplots(rows=rows, cols=cols)
imageCount = 0
for row in range(rows):
  for col in range(cols):
    fig.add_trace(
        go.Image(z=img[imageCount]),
        row=row+1, col=col+1
    )
    fig.update_yaxes(title_text=classes[y_train[imageCount]], row=row+1, col=col+1)
    imageCount+=1
fig.update_layout(height=1000)
fig.show()

# Experimentations

## basic model

In [276]:
basic = Sequential([
    layers.Flatten(input_shape=[150, 150,3]),
    layers.Dense(128,activation="relu"),
    layers.Dense(64,activation="relu"),
    layers.Dense(8,activation="softmax")
])

In [277]:
basic.compile(
    optimizer="adam",
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics="accuracy"
)

In [278]:
basic_history = basic.fit(
    X_train,
    y_train,
    epochs=15,
    validation_data=(X_val,y_val)
)

Epoch 1/15
125/125 [==============================] - 1s 7ms/step - loss: 1536.4718 - accuracy: 0.2105 - val_loss: 599.0464 - val_accuracy: 0.3380
Epoch 2/15
125/125 [==============================] - 1s 5ms/step - loss: 373.7020 - accuracy: 0.3128 - val_loss: 382.7700 - val_accuracy: 0.2960
Epoch 3/15
125/125 [==============================] - 1s 5ms/step - loss: 313.3602 - accuracy: 0.3498 - val_loss: 413.6548 - val_accuracy: 0.3580
Epoch 4/15
125/125 [==============================] - 1s 6ms/step - loss: 241.9473 - accuracy: 0.3708 - val_loss: 276.7520 - val_accuracy: 0.3510
Epoch 5/15
125/125 [==============================] - 1s 5ms/step - loss: 212.2269 - accuracy: 0.3790 - val_loss: 332.8355 - val_accuracy: 0.3480
Epoch 6/15
125/125 [==============================] - 1s 6ms/step - loss: 166.3642 - accuracy: 0.4083 - val_loss: 127.9121 - val_accuracy: 0.4130
Epoch 7/15
125/125 [==============================] - 1s 6ms/step - loss: 146.9402 - accuracy: 0.4280 - val_loss: 195.6789 

In [279]:
def plot_results(history):
  fig = make_subplots(rows=1, cols=2, subplot_titles=("model accuracy over epochs", "model loss over epochs"), horizontal_spacing = 0.25)

  fig.add_trace(
      go.Scatter(
          name='train accuracy',
          y=history.history['accuracy'],
          x=list(range(len(history.history['accuracy'])))
      ),
      row=1, col=1
  )
  fig.add_trace(
      go.Scatter(
          name='validation accuracy',
          y=history.history['val_accuracy'],
          x=list(range(len(history.history['val_accuracy'])))
      ),
      row=1, col=1
  )

  fig.add_trace(
      go.Scatter(
          name='train loss',
          y=history.history['loss'],
          x=list(range(len(history.history['loss'])))
      ),
      row=1, col=2
  )
  fig.add_trace(
      go.Scatter(
          name='validation loss',
          y=history.history['val_loss'],
          x=list(range(len(history.history['val_loss'])))
      ),
      row=1, col=2
  )
  
  fig.update_yaxes(title_text='accuracy', row=1, col=1)
  fig.update_xaxes(title_text='epochs', row=1, col=1)
  fig.update_yaxes(title_text='loss', row=1, col=2)
  fig.update_xaxes(title_text='epochs', row=1, col=2)
  fig.update_layout(height=600, width=800, title_text="results")
  
  fig.show()

plot_results(basic_history)

## CNN model

In [280]:
cnn = Sequential([
    layers.Convolution2D(64, (3, 3), dilation_rate=3, activation='relu',input_shape=(150,150,3)),
    layers.Convolution2D(32, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Convolution2D(16, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Convolution2D(8, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Flatten(),
    layers.Dense(activation='relu', units=128),
    layers.Dense(activation='relu', units=64),
    layers.Dense(activation='softmax', units=8),
])

In [281]:
cnn.compile(
    optimizer="adam",
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics="accuracy"
)

In [282]:
cnn_history=cnn.fit(
    X_train,
    y_train,
    epochs=15,
    validation_data=(X_val, y_val)
)

Epoch 1/15
125/125 [==============================] - 9s 64ms/step - loss: 2.4252 - accuracy: 0.1985 - val_loss: 1.6776 - val_accuracy: 0.3410
Epoch 2/15
125/125 [==============================] - 8s 62ms/step - loss: 1.5229 - accuracy: 0.4202 - val_loss: 1.3351 - val_accuracy: 0.4380
Epoch 3/15
125/125 [==============================] - 8s 62ms/step - loss: 1.1877 - accuracy: 0.5050 - val_loss: 1.3220 - val_accuracy: 0.4560
Epoch 4/15
125/125 [==============================] - 8s 63ms/step - loss: 0.8401 - accuracy: 0.6800 - val_loss: 1.2465 - val_accuracy: 0.5270
Epoch 5/15
125/125 [==============================] - 8s 63ms/step - loss: 0.6757 - accuracy: 0.7430 - val_loss: 1.2537 - val_accuracy: 0.5420
Epoch 6/15
125/125 [==============================] - 8s 64ms/step - loss: 0.5127 - accuracy: 0.8015 - val_loss: 1.2252 - val_accuracy: 0.5930
Epoch 7/15
125/125 [==============================] - 8s 64ms/step - loss: 0.3740 - accuracy: 0.8547 - val_loss: 1.3604 - val_accuracy: 0.5580

In [283]:
plot_results(cnn_history)

In [284]:
augmented = Sequential([
    tf.keras.layers.RandomRotation(0.1),
    tf.keras.layers.RandomFlip("horizontal_and_vertical"),
    layers.Convolution2D(64, (3 ,3), activation='relu',input_shape=(150, 150, 3)),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Convolution2D(32, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Convolution2D(16, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Convolution2D(8, (3, 3), activation='relu'),
    layers.MaxPool2D(pool_size=(2, 2)),
    layers.Flatten(),
    layers.Dense(activation='relu', units=128),
    layers.Dense(activation='relu', units=64),
    layers.Dense(activation='softmax', units=8),
])

In [285]:
augmented.compile(
    optimizer="adam",
    loss=tf.keras.losses.SparseCategoricalCrossentropy(),
    metrics="accuracy"
)

In [286]:
augmented_history=augmented.fit(
    X_train,
    y_train,
    epochs=30,
    validation_data=(X_val,y_val),
)

Epoch 1/30
125/125 [==============================] - 8s 57ms/step - loss: 2.2215 - accuracy: 0.2085 - val_loss: 1.8528 - val_accuracy: 0.2390
Epoch 2/30
125/125 [==============================] - 7s 54ms/step - loss: 1.7097 - accuracy: 0.2873 - val_loss: 1.5474 - val_accuracy: 0.3500
Epoch 3/30
125/125 [==============================] - 7s 54ms/step - loss: 1.5113 - accuracy: 0.3530 - val_loss: 1.4170 - val_accuracy: 0.3880
Epoch 4/30
125/125 [==============================] - 6s 51ms/step - loss: 1.3101 - accuracy: 0.4372 - val_loss: 1.1594 - val_accuracy: 0.4790
Epoch 5/30
125/125 [==============================] - 6s 51ms/step - loss: 1.0928 - accuracy: 0.5445 - val_loss: 0.9663 - val_accuracy: 0.6270
Epoch 6/30
125/125 [==============================] - 6s 51ms/step - loss: 0.9261 - accuracy: 0.6345 - val_loss: 0.7938 - val_accuracy: 0.6650
Epoch 7/30
125/125 [==============================] - 6s 51ms/step - loss: 0.7829 - accuracy: 0.6905 - val_loss: 0.6910 - val_accuracy: 0.7300

In [287]:
plot_results(augmented_history)